In [1]:
from CountryCountsByBatchcodeTable2BarChartDescriptionTableConverter import CountryCountsByBatchcodeTable2BarChartDescriptionTableConverter
from JensenShannonDistance2BarChartDescriptionColumnAdder import JensenShannonDistance2BarChartDescriptionColumnAdder
from CountriesByBatchcodeProvider import getCountryCountsByBatchcodeTable, filterByBatchcodes
from Column2DataframeAdder import addColumn2Dataframe
from BatchCodeTableFactory import BatchCodeTableFactory
from HistogramFactoryAndPersister import createAndSaveGlobalHistograms
from SymptomByBatchcodeTableFactory import SymptomByBatchcodeTableFactory
from BatchCodeTablePersister import createGlobalBatchCodeTable
from BatchCodeTableHtmlUpdater import updateBatchCodeTableHtmlFile, saveLastUpdated2HtmlFile
from InternationalVaersCovid19Provider import getInternationalVaersCovid19, getInternationalVaersCovid19BeforeDeletion, get_international_VAERSVAX_VAERSSYMPTOMS_Covid19
from DateProvider import DateProvider
from BarChartDescriptionTable2DictionaryConverter import BarChartDescriptionTable2DictionaryConverter
from CountryColumnsMerger import CountryColumnsMerger
from datetime import datetime
from VAERSFileDownloader import updateVAERSFiles
from GoogleAnalytics.CityCountsByBatchcodeTablesMerger import CityCountsByBatchcodeTablesMerger
from IOUtils import IOUtils
from pathlib import Path
from GoogleAnalytics.Helper import persistCityCountsByClickedBatchcodeTables
import os
import pandas as pd

pd.set_option('display.max_rows', 100)
pd.set_option('display.max_columns', None)

2025-01-17 13:20:53.212236: I tensorflow/core/platform/cpu_feature_guard.cc:193] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations:  SSE4.1 SSE4.2 AVX AVX2 AVX_VNNI FMA
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags.


In [2]:
# split --bytes=45MiB VAERSBeforeDeletion.7z VAERSBeforeDeletion_
def restoreVAERSBeforeDeletionFolder():
    os.system('mkdir -p VAERS')
    os.system('cat data/VAERSBeforeDeletion/VAERSBeforeDeletion_* > VAERS/VAERSBeforeDeletion.7z')
    os.system('cd VAERS; 7z x -y VAERSBeforeDeletion.7z')

vaersBeforeDeletionDataDir = 'VAERS/VAERSBeforeDeletion'
restoreVAERSBeforeDeletionFolder()


7-Zip 23.01 (x64) : Copyright (c) 1999-2023 Igor Pavlov : 2023-06-20
 64-bit locale=de_DE.UTF-8 Threads:16 OPEN_MAX:1048576

Scanning the drive for archives:
1 file, 334140194 bytes (319 MiB)

Extracting archive: VAERSBeforeDeletion.7z
--
Path = VAERSBeforeDeletion.7z
Type = 7z
Physical Size = 334140194
Headers Size = 549
Method = LZMA:23
Solid = +
Blocks = 1

Everything is Ok

Folders: 1
Files: 12
Size:       2810338133
Compressed: 334140194


In [3]:
print(datetime.now().strftime("%d.%m.%Y, %H:%M:%S Uhr"))

17.01.2025, 13:21:11 Uhr


In [ ]:
dateProvider = DateProvider()
print('          lastUpdated:', dateProvider.getLastUpdated())
print('lastUpdatedDataSource:', dateProvider.getLastUpdatedDataSource())
print('needsUpdate:', dateProvider.needsUpdate())


In [4]:
# FK-TODO: reactivate: years_from_start_of_COVID_vaccination_to_present = list(range(2020, datetime.now().year + 1))
years_from_start_of_COVID_vaccination_to_present = list(range(2020, datetime.now().year))


[2020, 2021, 2022, 2023, 2024]

In [ ]:
updateVAERSFiles(
        years = years_from_start_of_COVID_vaccination_to_present,
        workingDirectory = os.getcwd())

In [5]:
international_VAERSVAX_Covid19, international_VAERSSYMPTOMS = get_international_VAERSVAX_VAERSSYMPTOMS_Covid19(years = years_from_start_of_COVID_vaccination_to_present)

In [6]:
international_VAERSVAX_Covid19


VAX_TYPE         VAX_MANU  VAX_LOT VAX_DOSE_SERIES COUNTRY
VAERS_ID                                                           
902418    COVID19  PFIZER\BIONTECH   EH9899               1    <NA>
902440    COVID19  PFIZER\BIONTECH  EH 9899               1    <NA>
902446    COVID19  PFIZER\BIONTECH   EH9899               1    <NA>
902464    COVID19  PFIZER\BIONTECH   EH9899             UNK    <NA>
902465    COVID19  PFIZER\BIONTECH   EH9899               1    <NA>
...           ...              ...      ...             ...     ...
2818153   COVID19  PFIZER\BIONTECH   ER8731               2    <NA>
2818154   COVID19  PFIZER\BIONTECH   LN0588               1    <NA>
2818163   COVID19          MODERNA  AS7168B             UNK    <NA>
2818168   COVID19  PFIZER\BIONTECH   LN0588               1    <NA>
2818169   COVID19          MODERNA  3043259             UNK    <NA>

[1111189 rows x 5 columns]

In [7]:
international_VAERSSYMPTOMS


SYMPTOM1                           SYMPTOM2  \
VAERS_ID                                                              
855017                Arthralgia                             Chills   
855018                    Chills                            Fatigue   
855018         Muscular weakness                  Pain in extremity   
855019                      Pain                           Pruritus   
855020                    Chills             Influenza like illness   
...                          ...                                ...   
2812387                 Immobile  Immunoglobulin G4 related disease   
2812387   Polymyalgia rheumatica                                NaN   
2812411            Muscle spasms                                NaN   
2812443         Feeling abnormal                      Gingival pain   
2812443                Oral pain                        Pain in jaw   

                                                   SYMPTOM3  \
VAERS_ID                                                      
855017                                  Injection site pain   
855018                                         Hypertension   
855018                                              Pyrexia   
855019                                                 Rash   
855020                                              Myalgia   
...                                                     ...   
2812387   Loss of personal independence in daily activities   
2812387                                                 NaN   
2812411                                                 NaN   
2812443                                       Hyperhidrosis   
2812443                                     SARS-CoV-2 test   

                           SYMPTOM4                          SYMPTOM5  
VAERS_ID                                                               
855017                      Pyrexia                               NaN  
855018                Hypoaesthesia  Injected limb mobility decreased  
855018                       Tremor                           Vertigo  
855019                          NaN                               NaN  
855020            Pain in extremity                           Pyrexia  
...                             ...                               ...  
2812387   Musculoskeletal stiffness                 Parkinsonian gait  
2812387                         NaN                               NaN  
2812411                         NaN                               NaN  
2812443                     Illness                   Nasopharyngitis  
2812443                         NaN                               NaN  

[2750145 rows x 5 columns]

In [8]:
internationalVaersCovid19 = getInternationalVaersCovid19(dataDir = 'VAERS', years = years_from_start_of_COVID_vaccination_to_present)
internationalVaersCovid19

RECVDATE  DIED  L_THREAT  ER_VISIT  HOSPITAL  DISABLE   VAX_DATE  \
VAERS_ID                                                                      
902418   2020-12-15     0         0         0         0        0 2020-12-15   
902440   2020-12-15     0         0         0         0        0 2020-12-15   
902446   2020-12-15     0         0         0         0        0 2020-12-15   
902464   2020-12-15     0         0         0         0        0 2020-12-15   
902465   2020-12-15     0         0         0         0        0 2020-12-15   
...             ...   ...       ...       ...       ...      ...        ...   
2812387  2024-11-29     1         0         0         1        0 2023-01-11   
2812411  2024-11-29     0         0         0         0        0 2024-10-22   
2812411  2024-11-29     0         0         0         0        0 2024-10-22   
2812443  2024-11-29     0         0         0         0        1 2024-10-03   
2812443  2024-11-29     0         0         0         0        1 2024-10-03   

                           SPLTTYPE VAX_TYPE              VAX_MANU  \
VAERS_ID                                                             
902418                          NaN  COVID19       PFIZER\BIONTECH   
902440                          NaN  COVID19       PFIZER\BIONTECH   
902446                          NaN  COVID19       PFIZER\BIONTECH   
902464                          NaN  COVID19       PFIZER\BIONTECH   
902465                          NaN  COVID19       PFIZER\BIONTECH   
...                             ...      ...                   ...   
2812387   JPPFIZER INCPV20240015282  COVID19       PFIZER\BIONTECH   
2812411                         NaN  COVID19       PFIZER\BIONTECH   
2812411                         NaN  COVID19       PFIZER\BIONTECH   
2812443                         NaN  COVID19  UNKNOWN MANUFACTURER   
2812443                         NaN  COVID19  UNKNOWN MANUFACTURER   

                  VAX_LOT VAX_DOSE_SERIES        COUNTRY  SEVERE  
VAERS_ID                                                          
902418             EH9899               1  United States       0  
902440            EH 9899               1  United States       0  
902446             EH9899               1  United States       0  
902464             EH9899             UNK  United States       0  
902465             EH9899               1  United States       0  
...                   ...             ...            ...     ...  
2812387            GJ2675               5          Japan       1  
2812411            LK8836               1           <NA>       0  
2812411            LK8836               1           <NA>       0  
2812443   NO BATCH NUMBER             UNK           <NA>       1  
2812443   NO BATCH NUMBER             UNK           <NA>       1  

[1660122 rows x 14 columns]

In [9]:
internationalVaersCovid19 = CountryColumnsMerger.mergeCountryColumnOfSrcIntoDst(
    src = getInternationalVaersCovid19BeforeDeletion(vaersBeforeDeletionDataDir),
    dst = internationalVaersCovid19)
internationalVaersCovid19

RECVDATE  DIED  L_THREAT  ER_VISIT  HOSPITAL  DISABLE   VAX_DATE  \
VAERS_ID                                                                      
902418   2020-12-15     0         0         0         0        0 2020-12-15   
902440   2020-12-15     0         0         0         0        0 2020-12-15   
902446   2020-12-15     0         0         0         0        0 2020-12-15   
902464   2020-12-15     0         0         0         0        0 2020-12-15   
902465   2020-12-15     0         0         0         0        0 2020-12-15   
...             ...   ...       ...       ...       ...      ...        ...   
2818154  2024-12-26     0         0         0         0        0 2024-12-26   
2818162  2024-12-26     0         0         0         0        0 2024-11-01   
2818163  2024-12-26     0         0         0         0        1 2022-07-21   
2818168  2024-12-26     0         0         0         0        0 2024-12-26   
2818169  2024-12-26     0         0         0         0        0 2024-10-04   

         SPLTTYPE VAX_TYPE         VAX_MANU  VAX_LOT VAX_DOSE_SERIES  SEVERE  \
VAERS_ID                                                                       
902418        NaN  COVID19  PFIZER\BIONTECH   EH9899               1       0   
902440        NaN  COVID19  PFIZER\BIONTECH  EH 9899               1       0   
902446        NaN  COVID19  PFIZER\BIONTECH   EH9899               1       0   
902464        NaN  COVID19  PFIZER\BIONTECH   EH9899             UNK       0   
902465        NaN  COVID19  PFIZER\BIONTECH   EH9899               1       0   
...           ...      ...              ...      ...             ...     ...   
2818154       NaN  COVID19  PFIZER\BIONTECH   LN0588               1       0   
2818162       NaN  COVID19  PFIZER\BIONTECH     <NA>              7+       0   
2818163       NaN  COVID19          MODERNA  AS7168B             UNK       1   
2818168       NaN  COVID19  PFIZER\BIONTECH   LN0588               1       0   
2818169       NaN  COVID19          MODERNA  3043259             UNK       0   

                COUNTRY  
VAERS_ID                 
902418    United States  
902440    United States  
902446    United States  
902464    United States  
902465    United States  
...                 ...  
2818154   United States  
2818162   United States  
2818163   United States  
2818168   United States  
2818169   United States  

[1660122 rows x 14 columns]

In [10]:
chargenMonatsListe = internationalVaersCovid19[['VAX_LOT', 'VAX_DATE']]
chargenMonatsListe

VAX_LOT   VAX_DATE
VAERS_ID                    
902418     EH9899 2020-12-15
902440    EH 9899 2020-12-15
902446     EH9899 2020-12-15
902464     EH9899 2020-12-15
902465     EH9899 2020-12-15
...           ...        ...
2818154    LN0588 2024-12-26
2818162      <NA> 2024-11-01
2818163   AS7168B 2022-07-21
2818168    LN0588 2024-12-26
2818169   3043259 2024-10-04

[1660122 rows x 2 columns]

In [11]:
chargenMonatsListe = chargenMonatsListe[chargenMonatsListe['VAX_DATE'] >= pd.to_datetime('2020-01-01', format = '%Y-%m-%d')]
chargenMonatsListe

VAX_LOT   VAX_DATE
VAERS_ID                    
902418     EH9899 2020-12-15
902440    EH 9899 2020-12-15
902446     EH9899 2020-12-15
902464     EH9899 2020-12-15
902465     EH9899 2020-12-15
...           ...        ...
2818154    LN0588 2024-12-26
2818162      <NA> 2024-11-01
2818163   AS7168B 2022-07-21
2818168    LN0588 2024-12-26
2818169   3043259 2024-10-04

[1520691 rows x 2 columns]

In [12]:
chargenMonatsListe = chargenMonatsListe.value_counts(sort = False)
chargenMonatsListe

VAX_LOT    VAX_DATE  
!D0181     2021-06-11    1
# 009C01A  2021-05-14    1
# 015M20A  2021-02-16    1
# 048A21A  2021-02-16    1
# EN6201   2021-02-22    1
                        ..
ÉÑ6198     2021-03-01    1
Ø25A21A    2021-03-02    1
Ø27H21B    2021-12-27    1
Ø38B21A    2021-03-11    1
Ø94F21A    2022-01-07    1
Length: 220071, dtype: int64

In [13]:
chargenMonatsListe = chargenMonatsListe.reset_index(level = ['VAX_LOT'])
chargenMonatsListe

VAX_LOT  0
VAX_DATE                
2021-06-11     !D0181  1
2021-05-14  # 009C01A  1
2021-02-16  # 015M20A  1
2021-02-16  # 048A21A  1
2021-02-22   # EN6201  1
...               ... ..
2021-03-01     ÉÑ6198  1
2021-03-02    Ø25A21A  1
2021-12-27    Ø27H21B  1
2021-03-11    Ø38B21A  1
2022-01-07    Ø94F21A  1

[220071 rows x 2 columns]

In [14]:
chargenMonatsListe = chargenMonatsListe.rename(columns = {0: "count"})
chargenMonatsListe

VAX_LOT  count
VAX_DATE                    
2021-06-11     !D0181      1
2021-05-14  # 009C01A      1
2021-02-16  # 015M20A      1
2021-02-16  # 048A21A      1
2021-02-22   # EN6201      1
...               ...    ...
2021-03-01     ÉÑ6198      1
2021-03-02    Ø25A21A      1
2021-12-27    Ø27H21B      1
2021-03-11    Ø38B21A      1
2022-01-07    Ø94F21A      1

[220071 rows x 2 columns]

In [15]:
chargenMonatsListe = chargenMonatsListe.sort_index()
chargenMonatsListe

VAX_LOT  count
VAX_DATE                         
2020-01-01          EJ6796      1
2020-01-01          FD7958      1
2020-01-01         028L20A      1
2020-01-01  039(R OR K)20A      1
2020-01-01          FE3592      1
...                    ...    ...
2024-12-24         3044186      1
2024-12-26          LM2212      1
2024-12-26          LN0588      2
2024-12-26          LN0591      1
2024-12-26          LP1780      1

[220071 rows x 2 columns]

In [16]:
chargenMonatsListe = (chargenMonatsListe
                      .groupby([chargenMonatsListe.index.year, chargenMonatsListe.index.month, chargenMonatsListe['VAX_LOT']])
                      .sum())
chargenMonatsListe

count
VAX_DATE VAX_DATE VAX_LOT               
2020     1        #EL3247              1
                  004 M204             1
                  004M20A              2
                  004M2DA              1
                  011J20A              6
...                                  ...
2024     12       MOD-3044211          1
                  MODERNA COVID-1      1
                  NDC:00069-2432-      1
                  PAA226428            1
                  PFIZER 12+ NEW       1

[80771 rows x 1 columns]

In [17]:
chargenMonatsListe.index.set_names(['VAX_YEAR', 'VAX_MONTH', 'VAX_LOT'], inplace = True)
chargenMonatsListe

count
VAX_YEAR VAX_MONTH VAX_LOT               
2020     1         #EL3247              1
                   004 M204             1
                   004M20A              2
                   004M2DA              1
                   011J20A              6
...                                   ...
2024     12        MOD-3044211          1
                   MODERNA COVID-1      1
                   NDC:00069-2432-      1
                   PAA226428            1
                   PFIZER 12+ NEW       1

[80771 rows x 1 columns]

In [18]:
chargenMonatsListe = chargenMonatsListe.unstack(level = 2, fill_value = 0)

In [19]:
chargenMonatsListe = chargenMonatsListe[chargenMonatsListe.columns[chargenMonatsListe.sum() >= 100]]
chargenMonatsListe

count                                  \
VAX_LOT            000004A         000014A         000022A           
VAX_YEAR VAX_MONTH                                                   
2020     1                       0               0               0   
         2                       0               0               0   
         3                       0               0               0   
         4                       0               0               0   
         5                       0               0               0   
         6                       0               0               0   
         7                       0               0               0   
         8                       0               0               0   
         9                       0               0               0   
         10                      0               0               0   
         11                      0               0               0   
         12                      0               0               0   
2021     1                       1               6               0   
         2                       0               4               3   
         3                       0              16              15   
         4                       0               8               9   
         5                       4              10               9   
         6                       0               5              16   
         7                       2               0               3   
         8                       0               0               1   
         9                       0               0               0   
         10                      2               0               0   
         11                      1               1               1   
         12                     22             262             181   
2022     1                      62              49              46   
         2                      10               7               2   
         3                       1               0               0   
         4                       0               0               0   
         5                       0               0               0   
         6                       0               0               0   
         7                       0               0               0   
         8                       0               0               0   
         9                       0               0               0   
         10                      0               0               0   
         11                      0               0               0   
         12                      0               0               0   
2023     1                       0               0               0   
         2                       0               0               0   
         3                       0               0               0   
         4                       0               0               0   
         5                       0               0               0   
         6                       0               0               0   
         7                       0               0               0   
         8                       0               0               0   
         9                       0               0               0   
         10                      0               0               0   
         11                      0               0               0   
         12                      0               0               0   
2024     1                       0               0               0   
         2                       0               0               0   
         3                       0               0               0   
         4                       0               0               0   
         5                       0               0               0   
         6                       0               0               0   
         7                       0     

In [21]:
chargenMonatsListe.to_excel('ChargenMonatsListe-VAERS.xlsx')

In [ ]:
batchCodeTable = createGlobalBatchCodeTable(
    deleteEntriesWithADRsLessThanOrEqual = 2,
    minADRsForLethality = 100,
    batchCodeTableFactory = BatchCodeTableFactory(internationalVaersCovid19))
batchCodeTable

In [ ]:
IOUtils.saveDataFrameAsJson(batchCodeTable, '../docs/data/batchCodeTables/Global.json')
saveLastUpdated2HtmlFile(
    lastUpdated = dateProvider.getLastUpdatedDataSource(),
    htmlFile = "../docs/batchCodes.html",
    lastUpdatedElementId = 'last_updated')

In [ ]:
updateBatchCodeTableHtmlFile(
    batchCodeTable,
    batchCodeTableHtmlFile = "../docs/HowBadIsMyBatch.html",
    lastUpdated = dateProvider.getLastUpdatedDataSource())

In [ ]:
symptomByBatchcodeTable = SymptomByBatchcodeTableFactory.createSymptomByBatchcodeTable(
    VAERSVAX = international_VAERSVAX_Covid19[international_VAERSVAX_Covid19['VAX_LOT'].isin(batchCodeTable['Batch'])],
    VAERSSYMPTOMS = international_VAERSSYMPTOMS)
symptomByBatchcodeTable

In [ ]:
createAndSaveGlobalHistograms(symptomByBatchcodeTable, batchCodeTable)

In [ ]:
countryCountsByBatchcode = filterByBatchcodes(getCountryCountsByBatchcodeTable(vaersBeforeDeletionDataDir), batchCodeTable['Batch'].values)
countryCountsByBatchcode

In [ ]:
barChartDescriptionTable = CountryCountsByBatchcodeTable2BarChartDescriptionTableConverter.convert2BarChartDescriptionTable(countryCountsByBatchcode)
barChartDescriptionTable

In [ ]:
barChartDescriptionTable = JensenShannonDistance2BarChartDescriptionColumnAdder.addJensenShannonDistance2BarChartDescriptionColumn(barChartDescriptionTable)
barChartDescriptionTable

In [ ]:
IOUtils.saveDictAsJson(
    BarChartDescriptionTable2DictionaryConverter.convert2Dictionary(barChartDescriptionTable, internationalVaersCovid19),
    '../docs/data/barChartDescriptionTable.json')


# Google Analytics

In [ ]:
cityCountsByClickedBatchcodeTable = CityCountsByBatchcodeTablesMerger.getCityCountsByClickedBatchcode('data/GoogleAnalytics')
cityCountsByClickedBatchcodeTable

In [ ]:
# cityCountsByClickedBatchcodeTableIncludingDateRange = CityCountsByBatchcodeTablesMerger.getCityCountsByClickedBatchcode('data/GoogleAnalytics', includeDateRange = True)
# cityCountsByClickedBatchcodeTableIncludingDateRange.to_csv('cityCountsByClickedBatchcodeTableIncludingDateRange.csv')
# cityCountsByClickedBatchcodeTableIncludingDateRange

In [ ]:
persistCityCountsByClickedBatchcodeTables(
    dataDir = Path('tmp/cityCountsByClickedBatchcodeTables'),
    n = 10,
    cityCountsByClickedBatchcodeTable = cityCountsByClickedBatchcodeTable)
# import generated xlsx files in dataDir into https://www.google.com/mymaps

# Vaccine Distribution by Zipcode

In [ ]:
vaccineDistributionByZipcode  = pd.read_excel(
        io = 'data/Amended-22-01962-Pfizer-2022-0426-pulled-2022-0823.xlsx',
        usecols = ['PROVIDER_NAME', 'ZIPCODE_SHP', 'LOT_NUMBER', 'DOSES_SHIPPED'])
vaccineDistributionByZipcode

In [ ]:
from VaccineDistributionByZipcodeSimplifier import VaccineDistributionByZipcodeSimplifier

vaccineDistributionByZipcode = VaccineDistributionByZipcodeSimplifier.sumDoses(vaccineDistributionByZipcode)
vaccineDistributionByZipcode

In [ ]:
OVERALL_DOSES_SHIPPED_by_LOT_NUMBER = (
    vaccineDistributionByZipcode
        .groupby('LOT_NUMBER')
        .agg(OVERALL_DOSES_SHIPPED = pd.NamedAgg(column = 'DOSES_SHIPPED', aggfunc = sum)))
OVERALL_DOSES_SHIPPED_by_LOT_NUMBER

In [ ]:
vaccineDistributionByZipcode = addColumn2Dataframe(dataframe = vaccineDistributionByZipcode, column = OVERALL_DOSES_SHIPPED_by_LOT_NUMBER)
vaccineDistributionByZipcode

In [ ]:
from ADR_by_Batchcode_Table_Factory import create_ADR_by_Batchcode_Table_4USA

ADR_by_Batchcode_Table_4USA = create_ADR_by_Batchcode_Table_4USA(internationalVaersCovid19)
ADR_by_Batchcode_Table_4USA

In [ ]:
vaccineDistributionByZipcode = addColumn2Dataframe(dataframe = vaccineDistributionByZipcode, column = ADR_by_Batchcode_Table_4USA)
vaccineDistributionByZipcode

In [ ]:
vaccineDistributionByZipcode['Statistical Number of Adverse Reaction Reports'] = (vaccineDistributionByZipcode['DOSES_SHIPPED'] / vaccineDistributionByZipcode['OVERALL_DOSES_SHIPPED'] * vaccineDistributionByZipcode['Adverse Reaction Reports']).round(2)
vaccineDistributionByZipcode['Statistical Number of Adverse Reaction Reports (per 100,000)'] = (vaccineDistributionByZipcode['DOSES_SHIPPED'] / vaccineDistributionByZipcode['OVERALL_DOSES_SHIPPED'] * 100000).round().astype(int)
vaccineDistributionByZipcode

In [ ]:
vaccineDistributionByZipcode = vaccineDistributionByZipcode[['PROVIDER_NAME', 'ZIPCODE_SHP', 'LOT_NUMBER', 'DOSES_SHIPPED', 'Statistical Number of Adverse Reaction Reports', 'Statistical Number of Adverse Reaction Reports (per 100,000)']]
vaccineDistributionByZipcode

In [ ]:
vaccineDistributionByZipcode = vaccineDistributionByZipcode.rename(
    columns = {
        'PROVIDER_NAME': 'Provider',
        'ZIPCODE_SHP': 'ZIP Code',
        'LOT_NUMBER': 'Lot Number',
        'DOSES_SHIPPED': 'Doses Shipped'
    })
vaccineDistributionByZipcode

In [ ]:
# vaccineDistributionByZipcode.to_excel('tmp/Amended-22-01962-Pfizer-2022-0426-pulled-2022-0823_sumDoses.xlsx')


In [ ]:
IOUtils.saveDataFrameAsJson(vaccineDistributionByZipcode, '../docs/data/vaccineDistributionByZipcode/VaccineDistributionByZipcode.json')
saveLastUpdated2HtmlFile(
    lastUpdated = dateProvider.getLastUpdatedDataSource(),
    htmlFile =  "../docs/VaccineDistributionByZipcode.html",
    lastUpdatedElementId = 'last_updated')

# Symptoms caused by Drugs (EudraVigilance)


In [ ]:
from SymptomsCausedByVaccines.DataFrameFilter import DataFrameFilter
from SymptomsCausedByVaccines.HtmlUpdater import updateHtmlFile
from SymptomsCausedByVaccines.PrrSeriesFactory import PrrSeriesFactory
from SymptomsCausedByVaccines.PrrSeriesTransformer import PrrSeriesTransformer
from SymptomsCausedByVaccines.ProportionalReportingRatiosPersister import saveProportionalReportingRatios
import os
import pandas as pd
import gc

In [ ]:
def saveProportionalReportingRatios4PrrByVaccineBySymptomWithoutZeroPrrs(prrByVaccineAndSymptom, webAppBaseDir):
    prrByVaccineBySymptom = PrrSeriesFactory.getPrrByVaccineBySymptom(prrByVaccineAndSymptom)

    prrByVaccineBySymptomWithoutZeroPrrs = PrrSeriesTransformer.filterByNonZeroPrrs(prrByVaccineBySymptom)
    del prrByVaccineBySymptom
    gc.collect()

    filenameBySymptom = saveProportionalReportingRatios(
        prrByVaccineBySymptomWithoutZeroPrrs,
        directory = os.path.normpath(webAppBaseDir + '/data/ProportionalReportingRatios/symptoms'))

    del prrByVaccineBySymptomWithoutZeroPrrs
    gc.collect()
    return filenameBySymptom

In [ ]:
def saveProportionalReportingRatios4PrrBySymptomByVaccineWithHighPrrs(prrByVaccineAndSymptom, webAppBaseDir):
    prrBySymptomByVaccine = PrrSeriesFactory.getPrrBySymptomByVaccine(prrByVaccineAndSymptom)
    prrBySymptomByVaccineWithHighPrrs = PrrSeriesTransformer.filterPrrs(prrBySymptomByVaccine, lambda prr: prr >= 2)
    del prrBySymptomByVaccine
    gc.collect()

    filenameByDrug = saveProportionalReportingRatios(
        prrBySymptomByVaccineWithHighPrrs,
        directory = os.path.normpath(webAppBaseDir + '/data/ProportionalReportingRatios/vaccines'))

    del prrBySymptomByVaccineWithHighPrrs
    gc.collect()
    return filenameByDrug

In [ ]:
def saveProportionalReportingRatiosAndUpdateHtmlFile(prrByVaccineAndSymptom, webAppBaseDir, defaultSelectVaccineOptionText):
    prrByVaccineAndSymptom = DataFrameFilter.withoutZeroRowsAndZeroColumns(prrByVaccineAndSymptom)
    filenameBySymptom = saveProportionalReportingRatios4PrrByVaccineBySymptomWithoutZeroPrrs(prrByVaccineAndSymptom, webAppBaseDir)
    filenameByDrug = saveProportionalReportingRatios4PrrBySymptomByVaccineWithHighPrrs(prrByVaccineAndSymptom, webAppBaseDir)
    updateHtmlFile(
        symptomsDescr = {
            'symptoms': list(prrByVaccineAndSymptom.columns),
            'filenameBySymptom': filenameBySymptom },
        vaccinesDescr = {
            'vaccines': list(prrByVaccineAndSymptom.index),
            'filenameByDrug': filenameByDrug },
        htmlFile = os.path.normpath(webAppBaseDir + '/index.html'),
        defaultSelectVaccineOptionText = defaultSelectVaccineOptionText)


In [ ]:
os.system('cd data; 7z x -y prrByDrugAndSymptom-EudraVigilance.7z')

In [ ]:
prrByVaccineAndSymptom = pd.read_csv(
        'data/prrByDrugAndSymptom-EudraVigilance.csv',
        index_col = 'DRUG')
prrByVaccineAndSymptom.rename(
    columns = str.strip,
    inplace = True)
prrByVaccineAndSymptom

In [ ]:
saveProportionalReportingRatiosAndUpdateHtmlFile(
    prrByVaccineAndSymptom = prrByVaccineAndSymptom,
    webAppBaseDir = os.getcwd() + '/../docs/SymptomsCausedByDrugs',
    defaultSelectVaccineOptionText = 'Select Drug')

# Symptoms caused by Vaccines


In [ ]:
prrByVaccineAndSymptom = pd.read_csv(
    'data/tfiltered.csv',
    usecols = lambda x: x != "Unnamed: 0",
    index_col = 'VAX_TYPE')
prrByVaccineAndSymptom.index.name = 'VACCINE'
prrByVaccineAndSymptom

In [ ]:
saveProportionalReportingRatiosAndUpdateHtmlFile(
    prrByVaccineAndSymptom = prrByVaccineAndSymptom,
    webAppBaseDir = os.getcwd() + '/../docs/SymptomsCausedByVaccines',
    defaultSelectVaccineOptionText = 'Select Vaccine')

# Drugs for Pathologies

In [ ]:
import pandas as pd
import os
from DrugsForPathologies.DrugDescriptionsForPathologiesPersister import saveDrugDescriptionsForPathologies
from DrugsForPathologies.HtmlUpdater import updateHtmlFile as updateDrugsForPathologiesHtmlFile


In [ ]:
def getDrugDescrByPathology(drugs4Pathologies):
    def drugsTable2drugDescr(drugsTable):
        drugDescr = drugsTable.to_dict('list')
        del drugDescr['PATHOLOGY']
        return drugDescr
    
    return drugs4Pathologies.groupby('PATHOLOGY').apply(drugsTable2drugDescr)


In [ ]:
def saveDrugDescriptionsForPathologiesAndUpdateHtmlFile(drugDescrByPathology, webAppBaseDir):
    filenameByPathology = saveDrugDescriptionsForPathologies(
        drugDescrByPathology = drugDescrByPathology,
        directory = os.path.normpath(webAppBaseDir + '/data/DrugDescriptionsForPathologies'))
    updateDrugsForPathologiesHtmlFile(
        filenameByPathology,
        htmlFile = os.path.normpath(webAppBaseDir + '/index.html'))


In [ ]:
drugs4Pathologies  = pd.read_excel(
        io = 'data/1000-pathologies.xlsx',
        converters = {
            'PATHOLOGY': lambda text: text.strip(),
            'DRUG': lambda text: text.strip() })
drugs4Pathologies

In [ ]:
drugDescrByPathology = getDrugDescrByPathology(drugs4Pathologies)
drugDescrByPathology

In [ ]:
saveDrugDescriptionsForPathologiesAndUpdateHtmlFile(
    drugDescrByPathology = drugDescrByPathology,
    webAppBaseDir = os.path.normpath(os.getcwd() + '/../docs/DrugsForPathologies'))